In [1]:
# Core Libraries
import numpy as np  # Numerical operations and arrays.
import pandas as pd  # Data manipulation and analysis.
from io import StringIO  # String-based I/O operations.
import base64  # Encoding/decoding binary data.
from IPython.display import HTML  # Displaying HTML in Jupyter notebooks.

# Web Scraping Libraries
from bs4 import BeautifulSoup  # HTML and XML parsing.
import requests  # Making HTTP requests.

# Data Visualization and Dashboard Libraries
import panel as pn  # Interactive dashboards creation.
import hvplot.pandas  # Advanced plotting integrated with Pandas.

# Panel Configuration
pn.extension(sizing_mode="stretch_width")  # Sets dashboard width to full screen.

## Webscrape JEL Codes

In [2]:
# URL for economic classification codes.
url = 'https://cran.r-project.org/web/classifications/JEL.html'

# Fetch HTML content from URL.
response = requests.get(url)  # GET request.

# Parse HTML to BeautifulSoup object.
soup = BeautifulSoup(response.text, 'html.parser')  # HTML parsing.

# Select <li> elements with 'id' starting with 'code:'.
jel_codes = soup.find_all('li', id=lambda x: x and x.startswith('code:'))  # Filter for JEL codes.

# List to store JEL code descriptions.
jel_code_descriptions = []

# Extract descriptions from each JEL code element.
for code in jel_codes:
    jel_code = code['id'].split(':')[1]  # Extract code.
    if len(jel_code) == 3:  # Check code length.
        description = code.get_text(strip=True)  # Get text.
        jel_code_descriptions.append(description)  # Store description.
        

## Tab for Literature Search

In [3]:
# Loading dataset from CSV.
df = pd.read_csv('Derived/All-Journals-Cleaned.csv')

# Convert 'Journal' and 'Issue' columns to title case.
df['Journal'] = df['Journal'].str.title()
df['Issue'] = df['Issue'].str.title()

# Identifying columns for authors and JEL codes.
author_columns = [col for col in df.columns if col.startswith("Author")]
jel_columns = [col for col in df.columns if col.startswith("JEL")]

# Clean and deduplicate author names.
unique_authors = pd.unique(df[author_columns].values.ravel('K'))
unique_authors = [author for author in unique_authors if pd.notna(author)]

# Consolidate author information into one column and remove original columns.
df['Authors'] = df[author_columns].apply(lambda x: '; '.join(x.dropna()), axis=1)
df.drop(columns=author_columns, inplace=True)

# Consolidate JEL codes into one column and remove original columns.
df['JELs'] = df[jel_columns].apply(lambda x: '; '.join(x.dropna()), axis=1)
df.drop(columns=jel_columns, inplace=True)

# Create a list of years from 1999 to 2024.
years_list = list(range(1999, 2025))

# Extract unique journal names.
journal_list = df['Journal'].unique().tolist()

# Define a function to make URLs clickable.
def make_clickable(url, name):
    return f'<a target="_blank" href="{url}">{name}</a>'

# Apply clickable link function to the 'Link' column.
df['Link'] = df.apply(lambda row: make_clickable(row['Link'],row['Link']), axis=1)

# Convert DataFrame to HTML for display.
HTML(df.to_html(escape=False))

In [4]:
# Initialize interactive widgets for data filtering
year_input = pn.widgets.MultiChoice(name='Year(s)', options=years_list)  # Allows selection of years
journal_input = pn.widgets.MultiChoice(name='Journal(s)', options=journal_list)  # Allows selection of journals
author_input = pn.widgets.MultiChoice(name='Author(s)', options=unique_authors)  # Allows selection of authors
multi_choice = pn.widgets.MultiChoice(name='JEL Code(s)', options=jel_code_descriptions)  # Allows selection of JEL codes
abstract_search = pn.widgets.TextInput(name='Search Keyword(s)')  # Allows input of search keywords

# Variable to store the latest filtered DataFrame
global_filtered_df = None

def filter_data(selected_years, selected_journals, selected_jel_options, selected_authors, abstract_query):
    """
    Filters the DataFrame based on selected widget criteria.

    Args:
        selected_years (list): List of selected years.
        selected_journals (list): List of selected journals.
        selected_jel_options (list): List of selected JEL codes.
        selected_authors (list): List of selected authors.
        abstract_query (str): Input string for abstract search.

    Returns:
        DataFrame: Filtered DataFrame according to selected filters.
    """
    global global_filtered_df  # Reference global variable to store the filtered results
    filtered_df = df  # Start with the full dataset for filtering
    
    # Apply filters based on user selection from widgets
    if selected_years:
        year_strings = [str(year) for year in selected_years]
        filtered_df = filtered_df[filtered_df['Issue'].apply(lambda issue: any(year in issue for year in year_strings))]
        
    if selected_journals:
        filtered_df = filtered_df[filtered_df['Journal'].isin(selected_journals)]
    
    if selected_authors:
        # Ensure all selected authors must be present in the 'Authors' column for a row to be included
        filtered_df = filtered_df[filtered_df['Authors'].apply(lambda authors: all(author in authors for author in selected_authors))]

    if selected_jel_options:
        cleaned_jel_options = [option.split(':')[0] for option in selected_jel_options]
        filtered_df = filtered_df[filtered_df['JELs'].apply(lambda x: all(jel_option in x for jel_option in cleaned_jel_options))]
        
    if abstract_query:
        # Apply filter to relevant columns
        filtered_df = filtered_df[
            filtered_df['Abstract'].str.contains(abstract_query, case=False, na=False) |
            filtered_df['Title'].str.contains(abstract_query, case=False, na=False) |
            filtered_df['Issue'].str.contains(abstract_query, case=False, na=False) |
            filtered_df['Journal'].str.contains(abstract_query, case=False, na=False) |
            filtered_df['Authors'].str.contains(abstract_query, case=False, na=False)
        ]
    
    global_filtered_df = filtered_df[['Title', 'Issue', 'Journal', 'Abstract', 'Authors', 'Link']]
    
    # Stylize the DataFrame
    filtered_df = global_filtered_df.style.set_properties(**{'text-align': 'left'})
  
    return filtered_df

# Binds filter function with widgets to update display dynamically
dynamic_view = pn.bind(
    filter_data,
    selected_years=year_input.param.value,
    selected_journals=journal_input.param.value,
    selected_jel_options=multi_choice.param.value,
    selected_authors=author_input.param.value,
    abstract_query=abstract_search.param.value
)


In [5]:
def get_filtered_data():
    """
    Generates CSV data from the latest filtered DataFrame for downloading.
    
    Returns:
        StringIO: CSV data of the filtered DataFrame.
    """
    if global_filtered_df is not None:
        return StringIO(global_filtered_df.to_csv(index=False))  # Convert DataFrame to CSV
    return StringIO("Title,Issue,Journal,Abstract,Authors,Link\n")  # CSV header if no data


# Initialize FileDownload widget for filtered DataFrame download
download_button = pn.widgets.FileDownload(callback=get_filtered_data, filename="filtered_data.csv", button_type="primary")


In [6]:
# Text for the AEA Literature Search Tab
text_lit_search = """
# **Literature Search**

**Filter Database:**

Search literature by selecting criteria such as years, journals, JEL codes, authors, and keywords.

**Real-Time Updates:**

Display updates dynamically based on selected filters.

**Download Data:**

Download filtered literature data in CSV format.
"""

# Explanation text for the AEA Literature Search section
explanation_lit_search = """
For more information on the JEL Classification System, see [this website](https://www.aeaweb.org/econlit/jelCodes.php?view=jel).
"""

# Sidebar for the AEA Literature Search section
sidebar_lit_search = pn.layout.WidgetBox(
    pn.pane.Markdown(text_lit_search, margin=(0, 10)),
    year_input,
    journal_input,
    multi_choice,
    author_input,
    abstract_search,
    explanation_lit_search,
    download_button,
    max_width=350,
    sizing_mode='stretch_width'
).servable(area='sidebar')


## Template for the Website

In [7]:
# LOGO
file_path = 'logo.png'
mime_type = "image/png"

with open(file_path, "rb") as img_file:
    encoded_string = base64.b64encode(img_file.read()).decode('utf-8')
    
data_uri = f"data:{mime_type};base64,{encoded_string}"


In [8]:
tab0_content = pn.pane.Markdown("README", sizing_mode='stretch_width')
tab1_content = pn.pane.Markdown("Current Trends", sizing_mode='stretch_width')
tab2 = pn.Row(sidebar_lit_search, dynamic_view)
tab3_content = pn.pane.Markdown("Literature Review", sizing_mode='stretch_width')

# Create the Tabs object
tabs = pn.Tabs(
    ("README", tab0_content),
    ("Current Trends", tab1_content),
    ("Literature Search", tab2),
    ("Literature Review", tab3_content),
    sizing_mode='stretch_width'
)

layout = pn.template.FastListTemplate(
    title='Analyze AEA in a Super Cool Way',
    logo=data_uri,
    theme_toggle=False,
    main=pn.Column(tabs),
    accent='#622433'
)

# Make the layout available for serving or displaying
layout.show()


Launching server at http://localhost:65096
